In [29]:
!git clone https://github.com/2noise/ChatTTS.git

fatal: destination path 'ChatTTS' already exists and is not an empty directory.


In [30]:
%cd /content/ChatTTS

/content/ChatTTS


In [31]:
!pip install -r requirements.txt

In [32]:
!pip install ChatTTS

In [33]:
!pip install WeTextProcessing

In [34]:
import torch
torch._dynamo.config.cache_size_limit = 64 #设置了Dynamo缓存的大小限制为64MB，Dynamo缓存使用最近内核编译结果，加速后续相同或相似计算图的执行
torch._dynamo.config.suppress_errors = True #配置 Dynamo 在遇到无法优化的代码时，默认不抛出错误
torch.set_float32_matmul_precision('high') #浮点数矩阵乘法的精度为'high'

import ChatTTS
from IPython.display import Audio

In [35]:
chat = ChatTTS.Chat() #chat类实例
chat.load_models() #加载模型

In [36]:
texts = ["So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with.",]*3 \
        + ["我觉得像我们这些写程序的人，他，我觉得多多少少可能会对开源有一种情怀在吧我觉得开源是一个很好的形式。现在其实最先进的技术掌握在一些公司的手里的话，就他们并不会轻易的开放给所有的人用。"]*3

wavs = chat.infer(texts)  #推理

 NeMo-text-processing :: INFO     :: Creating ClassifyFst grammars.
INFO:NeMo-text-processing:Creating ClassifyFst grammars.
  0%|          | 0/384 [00:00<?, ?it/s]/usr/local/lib/python3.10/dist-packages/torch/overrides.py:110: UserWarning: 'has_cuda' is deprecated, please use 'torch.backends.cuda.is_built()'
  torch.has_cuda,
/usr/local/lib/python3.10/dist-packages/torch/overrides.py:111: UserWarning: 'has_cudnn' is deprecated, please use 'torch.backends.cudnn.is_available()'
  torch.has_cudnn,
/usr/local/lib/python3.10/dist-packages/torch/overrides.py:117: UserWarning: 'has_mps' is deprecated, please use 'torch.backends.mps.is_built()'
  torch.has_mps,
/usr/local/lib/python3.10/dist-packages/torch/overrides.py:118: UserWarning: 'has_mkldnn' is deprecated, please use 'torch.backends.mkldnn.is_available()'
  torch.has_mkldnn,
[2024-06-04 02:26:52,219] torch._dynamo.convert_frame: [WARNING] WON'T CONVERT forward /usr/local/lib/python3.10/dist-packages/transformers/models/llama/modeling_

In [37]:
Audio(wavs[0], rate=24_000, autoplay=True)  #播放音频

In [38]:
Audio(wavs[3], rate=24_000, autoplay=True)

In [39]:
params_infer_code = {'prompt':'[speed_5]', 'temperature':.3}
params_refine_text = {'prompt':'[oral_2][laugh_0][break_6]'}

wav = chat.infer('四川美食可多了，有麻辣火锅、宫保鸡丁、麻婆豆腐、担担面、回锅肉、夫妻肺片等，每样都让人垂涎三尺。', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)

 19%|█▉        | 396/2048 [00:12<00:50, 32.81it/s]


In [40]:
Audio(wav[0], rate=24_000, autoplay=True)

In [41]:
rand_spk = chat.sample_random_speaker()
params_infer_code = {'spk_emb' : rand_spk, }

wav = chat.infer('四川美食确实以辣闻名，但也有不辣的选择。比如甜水面、赖汤圆、蛋烘糕、叶儿粑等，这些小吃口味温和，甜而不腻，也很受欢迎。', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)

 28%|██▊       | 576/2048 [00:17<00:45, 32.08it/s]


In [42]:
Audio(wav[0], rate=24_000, autoplay=True)

In [43]:
text = "So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with."
chat.infer(text, refine_text_only=True)

 22%|██▏       | 83/384 [00:02<00:08, 35.77it/s]


['so we found being [uv_break] competitive and collaborative [uv_break] was a huge way of staying motivated towards our goals, [uv_break] so one person to call [uv_break] when you fall off, [uv_break] one person who gets you back on [uv_break] then one person to actually do the activity with.']

In [44]:
text = 'so we found being competitive and collaborative [uv_break] was a huge way of staying [uv_break] motivated towards our goals, [uv_break] so [uv_break] one person to call [uv_break] when you fall off, [uv_break] one person who [uv_break] gets you back [uv_break] on then [uv_break] one person [uv_break] to actually do the activity with.'
wav = chat.infer(text, skip_refine_text=True)

 51%|█████     | 1038/2048 [00:31<00:30, 33.12it/s]


In [45]:
Audio(wav[0], rate=24_000, autoplay=True)

In [46]:
!pip install torchaudio

In [47]:
import ChatTTS
from IPython.display import Audio
import torchaudio
import torch

chat = ChatTTS.Chat()
chat.load_models(compile=False) # 设置为True以获得更快速度

texts = ["在这里输入你的文本[laugh][lbreak]",]

wavs = chat.infer(texts, use_decoder=True)

torchaudio.save("output1.wav", torch.from_numpy(wavs[0]), 24000)

  8%|▊         | 174/2048 [00:05<00:54, 34.34it/s]


In [48]:
###################################
# Sample a speaker from Gaussian.

rand_spk = chat.sample_random_speaker()

params_infer_code = {
  'spk_emb': rand_spk, # add sampled speaker
  'temperature': .3, # using custom temperature
  'top_P': 0.7, # top P decode
  'top_K': 20, # top K decode
}

In [49]:
###################################
# For sentence level manual control.

# use oral_(0-9), laugh_(0-2), break_(0-7)
# to generate special token in text to synthesize.
params_refine_text = {
  'prompt': '[oral_2][laugh_0][break_6]'
}

wav = chat.infer(texts, params_refine_text=params_refine_text, params_infer_code=params_infer_code)

  7%|▋         | 137/2048 [00:03<00:50, 37.51it/s]


In [50]:
Audio(wavs[0], rate=24_000, autoplay=True)

In [51]:
!pip install nemo_text_processing

In [52]:
from nemo_text_processing.text_normalization import Normalizer

In [53]:
###################################
# For word level manual control.
# use_decoder=False to infer faster with a bit worse quality
text = 'What is [uv_break]your favorite english food?[laugh][lbreak]'
wav = chat.infer(text, skip_refine_text=True, params_infer_code=params_infer_code, use_decoder=False)

torchaudio.save("output2.wav", torch.from_numpy(wavs[0]), 24000)

 NeMo-text-processing :: INFO     :: Creating ClassifyFst grammars.
INFO:NeMo-text-processing:Creating ClassifyFst grammars.
  8%|▊         | 174/2048 [00:04<00:46, 39.94it/s]


In [54]:
Audio(wavs[0], rate=24_000, autoplay=True)

In [55]:
inputs_cn = """
chat T T S 是一款强大的对话式文本转语音模型。它有中英混读和多说话人的能力。
chat T T S 不仅能够生成自然流畅的语音，还能控制[laugh]笑声啊[laugh]，
停顿啊[uv_break]语气词啊等副语言现象[uv_break]。这个韵律超越了许多开源模型[uv_break]。
请注意，chat T T S 的使用应遵守法律和伦理准则，避免滥用的安全风险。[uv_break]'
""".replace('\n', '')

params_refine_text = {
  'prompt': '[oral_2][laugh_0][break_4]'
}
audio_array_cn = chat.infer(inputs_cn, params_refine_text=params_refine_text)
# audio_array_en = chat.infer(inputs_en, params_refine_text=params_refine_text)

torchaudio.save("output3.wav", torch.from_numpy(audio_array_cn[0]), 24000)

 56%|█████▌    | 1143/2048 [00:37<00:29, 30.82it/s]


In [56]:
!pip install gradio

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.3/12.3 MB 91.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.0/92.0 kB 15.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 316.3/316.3 kB 42.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 12.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 142.5/142.5 kB 23.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.8/8.8 MB 91.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 47.2/47.2 kB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.4/62.4 kB 11.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.9/129.9 kB 22.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 12.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 11.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 71.9/71.9 kB 11.1 M

In [57]:
!pip uninstall Typer

Found existing installation: typer 0.12.3
Uninstalling typer-0.12.3:
  Would remove:
    /usr/local/bin/typer
    /usr/local/lib/python3.10/dist-packages/typer-0.12.3.dist-info/*
    /usr/local/lib/python3.10/dist-packages/typer/*
Proceed (Y/n)? y
  Successfully uninstalled typer-0.12.3


In [58]:
!pip install Typer==0.9.4

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.0/46.0 kB 1.4 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
fastapi-cli 0.0.4 requires typer>=0.12.3, but you have typer 0.9.4 which is incompatible.
gradio 4.32.2 requires typer<1.0,>=0.12; sys_platform != "emscripten", but you have typer 0.9.4 which is incompatible.


In [60]:
!python webui.py

INFO:httpx:HTTP Request: GET https://checkip.amazonaws.com/ "HTTP/1.1 200 "
loading ChatTTS model...
INFO:ChatTTS.core:Load from cache: /root/.cache/huggingface/hub/models--2Noise--ChatTTS/snapshots/d7474137acb4f988874e5d57ad88d81bcb7e10b6
INFO:ChatTTS.core:use cuda:0
INFO:ChatTTS.core:vocos loaded.
INFO:ChatTTS.core:dvae loaded.
INFO:httpx:HTTP Request: GET https://api.gradio.app/pkg-version "HTTP/1.1 200 OK"
INFO:ChatTTS.core:gpt loaded.
INFO:ChatTTS.core:decoder loaded.
INFO:ChatTTS.core:tokenizer loaded.
INFO:ChatTTS.core:All initialized.
Running on local URL:  http://0.0.0.0:8000
INFO:httpx:HTTP Request: GET http://localhost:8000/startup-events "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: HEAD http://localhost:8000/ "HTTP/1.1 200 OK"

To create a public link, set `share=True` in `launch()`.
Keyboard interruption in main thread... closing server.
Process ForkProcess-2:
Process ForkProcess-1:
Traceback (most recent call last):
  File "/usr/lib/python3.10/multiprocessing/process.py", l